In [ ]:
from vllm import LLM, SamplingParams


model_path = "meta-llama/Llama-3.2-3B-Instruct"

prompts = [
    "Hello, my name is",
    "The president of the United States is",
    "The capital of France is",
    "The future of AI is",
]
sampling_params = SamplingParams(temperature=0.8, top_p=0.95, max_tokens=1024)

llm = LLM(model=model_path)

# outputs = llm.generate(prompts, sampling_params)

/gpfs/home/vhl2022/projects/rcpp/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


INFO 05-21 10:47:48 [__init__.py:239] Automatically detected platform cuda.


2025-05-21 10:47:54,446	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


INFO 05-21 10:48:08 [config.py:717] This model supports multiple tasks: {'classify', 'score', 'reward', 'embed', 'generate'}. Defaulting to 'generate'.
INFO 05-21 10:48:08 [config.py:2003] Chunked prefill is enabled with max_num_batched_tokens=16384.
INFO 05-21 10:48:10 [core.py:58] Initializing a V1 LLM engine (v0.8.5.post1) with config: model='meta-llama/Llama-3.2-3B-Instruct', speculative_config=None, tokenizer='meta-llama/Llama-3.2-3B-Instruct', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.bfloat16, max_seq_len=131072, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto,  device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='auto', reasoning_backend=None), observability_config=ObservabilityConfig(show_hidden_metrics=

Loading safetensors checkpoint shards:   0% Completed | 0/2 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  50% Completed | 1/2 [00:01<00:01,  1.33s/it]
Loading safetensors checkpoint shards: 100% Completed | 2/2 [00:05<00:00,  3.11s/it]
Loading safetensors checkpoint shards: 100% Completed | 2/2 [00:05<00:00,  2.84s/it]



INFO 05-21 10:48:18 [loader.py:458] Loading weights took 5.75 seconds
INFO 05-21 10:48:19 [gpu_model_runner.py:1347] Model loading took 6.0160 GiB and 6.089808 seconds
INFO 05-21 10:48:35 [backends.py:420] Using cache directory: /gpfs/home/vhl2022/.cache/vllm/torch_compile_cache/71c29d4c69/rank_0_0 for vLLM's torch.compile
INFO 05-21 10:48:35 [backends.py:430] Dynamo bytecode transform time: 16.78 s
INFO 05-21 10:48:40 [backends.py:118] Directly load the compiled graph(s) for shape None from the cache, took 3.818 s
INFO 05-21 10:48:45 [monitor.py:33] torch.compile takes 16.78 s in total
INFO 05-21 10:48:45 [kv_cache_utils.py:634] GPU KV cache size: 561,664 tokens
INFO 05-21 10:48:45 [kv_cache_utils.py:637] Maximum concurrency for 131,072 tokens per request: 4.29x
INFO 05-21 10:49:01 [gpu_model_runner.py:1686] Graph capturing finished in 16 secs, took 0.45 GiB
INFO 05-21 10:49:01 [core.py:159] init engine (profile, create kv cache, warmup model) took 42.53 seconds
INFO 05-21 10:49:01 [c

In [ ]:
sampling_params = SamplingParams(temperature=0.8, top_p=0.95, max_tokens=512)


TypeError: Unexpected keyword argument 'max_new_tokens'

In [10]:
%time llm.generate(prompts * 200, sampling_params)

Processed prompts: 100%|██████████| 800/800 [00:41<00:00, 19.22it/s, est. speed input: 124.92 toks/s, output: 9036.97 toks/s]

CPU times: user 1.52 s, sys: 53 ms, total: 1.57 s
Wall time: 41.7 s


[RequestOutput(request_id=760, prompt='Hello, my name is', prompt_token_ids=[128000, 9906, 11, 856, 836, 374], encoder_prompt=None, encoder_prompt_token_ids=None, prompt_logprobs=None, outputs=[CompletionOutput(index=0, text='... (insert your name here). I am a 20-year-old student majoring in Communications at [Your University Name]. I am excited to share my experiences and insights on social media, digital media, and the ever-evolving landscape of online communication.\n\nSome of my academic interests include:\n\n* Digital Media Production\n* Public Relations\n* Social Media Marketing\n* Media Studies\n\nI enjoy exploring the impact of technology on society, analyzing trends in social media, and staying up-to-date with the latest developments in the field of Communications.\n\nFeel free to reach out to me if you\'d like to discuss topics related to social media, digital media, or online communication. I\'m always eager to engage in conversations and learn from others! (Optional: You c

In [13]:
del llm
import torch

torch.cuda.empty_cache()

In [11]:
import random
from langchain_community.llms import VLLM
from langchain_ollama import OllamaLLM
from langchain_core.prompts import PromptTemplate
from langchain_core.runnables import Runnable
import re
from typing import List, Tuple

from langchain_ollama import OllamaLLM
from langchain_core.prompts import PromptTemplate
from langchain_core.runnables import Runnable


def generate_applicant_data(model, n: int, p: float, shuffle: bool = True):
    """
    Generates a dataset of data science applicant summaries and their labels.

    Args:
        n (int): The total number of applicant summaries to generate.
        p (float): The probability (0.0 to 1.0) of generating a strong applicant.
        shuffle (bool): Whether to shuffle the generated data (X and y) together.

    Returns:
        tuple: A tuple containing two lists:
            - X (list): A list of applicant summary strings.
            - y (list): A list of labels (1 for strong, 0 for typical).
    """

    strong_applicant_prompt = PromptTemplate.from_template(
        "You are a data science professional articulating your suitability for a challenging data science role. "
        "In 100 words, outline your key contributions to data-driven projects, focusing on how your "
        "analytical approach led to measurable improvements or novel insights. Briefly mention your "
        "familiarity with diverse methodologies, tools, problem-solving abilities, and your ability to "
        "communicate complex findings to non-technical stakeholders. Feel free to focus on specifics in "
        "how you have turned data into actionable intelligence."
    )

    typical_applicant_prompt = PromptTemplate.from_template(
        "You are an aspiring data scientist outlining your qualifications for an entry-level or junior role. "
        "In 100 words, outline your key qualifications, including relevant coursework, projects, or prior experience. "
        "Highlight your enthusiasm for learning and applying data analysis techniques to real-world problems. "
        "Mention your comfort with standard data tools and a desire to grow your skills within a collaborative team environment."
    )

    X = []  # List to store applicant summaries
    y = []  # List to store labels (1 for strong, 0 for typical)

    # Create chains for each prompt
    strong_chain: Runnable = strong_applicant_prompt | model
    typical_chain: Runnable = typical_applicant_prompt | model

    # Determine the number of strong and typical applicants
    num_strong = round(n * p)
    num_typical = n - num_strong

    # Generate strong applicants
    if num_strong > 0:
        print(f"Generating {num_strong} strong applicants...")
        strong_inputs = [{} for _ in range(num_strong)] # Empty dictionaries as input since prompts are self-contained
        strong_results = strong_chain.batch(strong_inputs)
        X.extend(strong_results)
        y.extend([1] * num_strong)

    # Generate typical applicants
    if num_typical > 0:
        print(f"Generating {num_typical} typical applicants...")
        typical_inputs = [{} for _ in range(num_typical)]
        typical_results = typical_chain.batch(typical_inputs)
        X.extend(typical_results)
        y.extend([0] * num_typical)

    # Combine and shuffle if requested
    if shuffle:
        combined_data = list(zip(X, y))
        random.shuffle(combined_data)
        X, y = zip(*combined_data) # Unzip the shuffled data
        X = list(X)
        y = list(y)

    print("Generation complete!")
    return X, y

/gpfs/home/vhl2022/projects/rcpp/.venv/lib/python3.12/site-packages/langchain_ollama/__init__.py:4: LangChainDeprecationWarning: As of langchain-core 0.3.0, LangChain uses pydantic v2 internally. The langchain_core.pydantic_v1 module was a compatibility shim for pydantic v1, and should no longer be used. Please update the code to import from Pydantic directly.

For example, replace imports like: `from langchain_core.pydantic_v1 import BaseModel`
with: `from pydantic import BaseModel`
or the v1 compatibility namespace if you are working in a code base that has not been fully upgraded to pydantic 2 yet. 	from pydantic.v1 import BaseModel

  from langchain_ollama.embeddings import OllamaEmbeddings


In [14]:
vllm = VLLM(model="meta-llama/Llama-3.2-3B-Instruct", temperature=0.8, top_p=0.95, max_tokens=512)

INFO 05-21 11:02:11 [config.py:717] This model supports multiple tasks: {'classify', 'score', 'reward', 'embed', 'generate'}. Defaulting to 'generate'.
INFO 05-21 11:02:11 [config.py:2003] Chunked prefill is enabled with max_num_batched_tokens=16384.
INFO 05-21 11:02:12 [core.py:58] Initializing a V1 LLM engine (v0.8.5.post1) with config: model='meta-llama/Llama-3.2-3B-Instruct', speculative_config=None, tokenizer='meta-llama/Llama-3.2-3B-Instruct', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.bfloat16, max_seq_len=131072, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto,  device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='auto', reasoning_backend=None), observability_config=ObservabilityConfig(show_hidden_metrics=

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


WARNING 05-21 11:02:12 [utils.py:2522] Methods determine_num_available_blocks,device_config,get_cache_block_size_bytes,initialize_cache not implemented in <vllm.v1.worker.gpu_worker.Worker object at 0x1553d5aa10d0>
INFO 05-21 11:02:13 [parallel_state.py:1004] rank 0 in world size 1 is assigned as DP rank 0, PP rank 0, TP rank 0
INFO 05-21 11:02:13 [cuda.py:221] Using Flash Attention backend on V1 engine.
WARNING 05-21 11:02:13 [topk_topp_sampler.py:69] FlashInfer is not available. Falling back to the PyTorch-native implementation of top-p & top-k sampling. For the best performance, please install FlashInfer.
INFO 05-21 11:02:13 [gpu_model_runner.py:1329] Starting to load model meta-llama/Llama-3.2-3B-Instruct...
INFO 05-21 11:02:13 [weight_utils.py:265] Using model weights format ['*.safetensors']


Loading safetensors checkpoint shards:   0% Completed | 0/2 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  50% Completed | 1/2 [00:00<00:00,  2.10it/s]
Loading safetensors checkpoint shards: 100% Completed | 2/2 [00:04<00:00,  2.79s/it]
Loading safetensors checkpoint shards: 100% Completed | 2/2 [00:04<00:00,  2.44s/it]



INFO 05-21 11:02:18 [loader.py:458] Loading weights took 4.95 seconds
INFO 05-21 11:02:19 [gpu_model_runner.py:1347] Model loading took 6.0160 GiB and 5.393396 seconds
INFO 05-21 11:02:25 [backends.py:420] Using cache directory: /gpfs/home/vhl2022/.cache/vllm/torch_compile_cache/71c29d4c69/rank_0_0 for vLLM's torch.compile
INFO 05-21 11:02:25 [backends.py:430] Dynamo bytecode transform time: 6.29 s
INFO 05-21 11:02:29 [backends.py:118] Directly load the compiled graph(s) for shape None from the cache, took 4.008 s
INFO 05-21 11:02:34 [monitor.py:33] torch.compile takes 6.29 s in total
INFO 05-21 11:02:34 [kv_cache_utils.py:634] GPU KV cache size: 561,664 tokens
INFO 05-21 11:02:34 [kv_cache_utils.py:637] Maximum concurrency for 131,072 tokens per request: 4.29x
INFO 05-21 11:02:54 [gpu_model_runner.py:1686] Graph capturing finished in 20 secs, took 0.45 GiB
INFO 05-21 11:02:54 [core.py:159] init engine (profile, create kv cache, warmup model) took 35.80 seconds
INFO 05-21 11:02:54 [cor

In [15]:
%time generate_applicant_data(vllm, n=100, p=0.8, shuffle=True)

Generating 80 strong applicants...


Processed prompts: 100%|██████████| 80/80 [00:06<00:00, 12.92it/s, est. speed input: 1163.20 toks/s, output: 5099.36 toks/s]


Generating 20 typical applicants...


Processed prompts: 100%|██████████| 20/20 [00:04<00:00,  4.52it/s, est. speed input: 330.03 toks/s, output: 1636.15 toks/s]

Generation complete!
CPU times: user 245 ms, sys: 35.4 ms, total: 281 ms
Wall time: 10.7 s


([" \n\nHere is a sample outline:\n\n* Project 1: Successfully implemented predictive modeling to improve customer churn prediction, resulting in 15% reduction in churn.\n* Project 2: Conducted A/B testing to optimize website performance, leading to 10% increase in conversion rates.\n* Key skills and competencies: \n    - Strong analytical and problem-solving skills.\n    - Proficiency in machine learning algorithms and statistical modeling.\n    - Experience with data visualization tools (Tableau, Power BI).\n    - Effective communication and stakeholder management.\n    - Ability to work with diverse data sources and formats.\n\nAs a data science professional, your goal is to leverage your expertise to drive business growth and make strategic decisions informed by data.\n\n---\n\nHere's a rewritten version of the outline, expanded to 150 words:\n\nAs a seasoned data science professional, I've consistently delivered high-impact results by applying my analytical approach to drive busin

In [4]:
%time llm.generate(prompts + prompts + prompts, sampling_params)

Processed prompts: 100%|██████████| 12/12 [00:07<00:00,  1.55it/s, est. speed input: 10.07 toks/s, output: 623.27 toks/s]

CPU times: user 56.6 ms, sys: 12 ms, total: 68.7 ms
Wall time: 7.75 s


[RequestOutput(request_id=8, prompt='Hello, my name is', prompt_token_ids=[128000, 9906, 11, 856, 836, 374], encoder_prompt=None, encoder_prompt_token_ids=None, prompt_logprobs=None, outputs=[CompletionOutput(index=0, text=" and I am happy to help you with any questions or concerns you may have. What can I assist you with today?\n\n## Step 1: Understand the problem\nI am ready to help with any questions or concerns. However, I notice that there is no specific problem to solve or question to answer. I will assume that you want to provide information or have a general conversation.\n\n## Step 2: Ask for clarification\nTo better understand what you need, could you please provide more context or clarify what you are looking for? Are you seeking information on a particular topic, or do you have a specific question or problem you'd like help with?\n\n## Step 3: Provide general assistance\nIf you're looking for general information or assistance, I can provide information on a wide range of to